# Film gross analysis

Problem statement: Determine cumulative box office performance of a given theatrical title, using historical theatrical box office performance data & reviews data. Perform from the timeline from 2007 - present. 

Hypothesis:
Strong correlations exist between pre-release metrics and performance in the theatrical marketplace, but inevitable variability in model performance based on strong, difficult to capture factors (film cast, economy, ultra-specific seasonality)

The overall goal isn't to build a perfect model - it's to best understand the relationship between box office and review scores to see how well correlated they are, and to potentially bring in some other film metadata to strengthen the relationship of the variables to propose a model.

There are two notebooks here. One is this one, the other is a webscraper for metacritic scores. This notebook will tell the reviewer when to check the other. 

## Import libraries

In [5]:
%matplotlib inline 
import warnings
warnings.filterwarnings('ignore')

import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import seaborn as sns
import time
import re
from IPython.display import Image, Markdown, display
from fuzzywuzzy import fuzz
from fuzzywuzzy import process
from sklearn.linear_model import LogisticRegression
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import cross_val_predict
from sklearn.metrics import accuracy_score, precision_score, classification_report
from sklearn.linear_model import ElasticNet, Ridge, Lasso
from sklearn.neighbors import KNeighborsClassifier
from sklearn.grid_search import GridSearchCV
from sklearn.cross_validation import KFold
from sklearn.metrics import precision_recall_curve, roc_curve, roc_auc_score, auc
from sklearn.feature_selection import SelectPercentile
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier, VotingClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.naive_bayes import GaussianNB
from sklearn.neighbors import KNeighborsRegressor
from sklearn.metrics import classification_report
from sklearn.grid_search import GridSearchCV

pd.options.display.max_rows = 999
pd.options.mode.chained_assignment = None

## EDA

Goals will be to clean data via identifying data types & designating them properly, addressing nulls, and dummifying variables when necessary. Also developing functions for future use & scale.

In [6]:
# Import the data, set a master copy in case
df_master = pd.read_csv('data/filmgrosses.csv')
df = df_master.copy()

In [7]:
# Inspect the data
# Missing values, lots of objects
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7907 entries, 0 to 7906
Data columns (total 28 columns):
Title                             7907 non-null object
Rating                            7610 non-null object
Academy Awards                    108 non-null object
Actors                            6178 non-null object
Categories                        7875 non-null object
Detailed_Release                  7844 non-null object
Directors                         7761 non-null object
Dist                              7907 non-null object
Distributor Long Name             7907 non-null object
Year(DVD/Video Release Date)      5249 non-null float64
Golden Globes                     69 non-null object
Language                          7793 non-null object
Producers                         6069 non-null object
Production Companies              2449 non-null object
Quarter(Release Date)             7674 non-null object
Sound Formats                     4638 non-null object
Visual Formats 

In [8]:
# Inspect the data, one observation
# Some data points represented as lists (with commas)
# Some non-integer columns (also with commas)
df.iloc[182]

Title                                                                      whiplash
Rating                                                                            r
Academy Awards                    best film editing, best sound mixing, best sup...
Actors                            j.k. simmons, melissa benoist, miles teller, p...
Categories                                                                    drama
Detailed_Release                                                         10/10/2014
Directors                                                           damien chazelle
Dist                                                                            spc
Distributor Long Name                                        sony pictures classics
Year(DVD/Video Release Date)                                                   2015
Golden Globes                                                 best supporting actor
Language                                                                    

In [9]:
# Data cleaning will need to occur. Review columns with multiple values
# This occurs for the three variables below:

collist1 = ['Academy Awards', 'Categories','Golden Globes']
for i in collist1:
    display(Markdown(("""### """+i)))
    print(df[i].value_counts())

### Academy Awards

best documentary                                                                                                                          9
best supporting actress                                                                                                                   7
best animated feature film                                                                                                                7
best actress                                                                                                                              5
best costume design                                                                                                                       4
best original screenplay                                                                                                                  4
best visual effects                                                                                                                       4
best adapted screenp

### Categories

documentary                                                                             1614
drama                                                                                   1197
comedy                                                                                   723
horror, suspense                                                                         296
comedy, drama                                                                            241
suspense                                                                                 207
special events                                                                           197
documentary, foreign                                                                     147
drama, suspense                                                                          138
drama, romance                                                                           134
comedy, romance                                                       

### Golden Globes

best actress - drama                                                                                                                  8
best actor - drama                                                                                                                    7
best supporting actress                                                                                                               6
best supporting actor                                                                                                                 6
best actor - musical or comedy                                                                                                        4
best actress - musical or comedy                                                                                                      4
best actor - musical or comedy, best picture - musical or comedy                                                                      3
best screenplay                                 

In [10]:
# Create function to split variables represent multiple desginations (i.e., two academy awards), and allow them to
# exist independently 

# Step 1: Create a list of all unique possibilities for the variable
# Step 2: Create the columns to house
# Step 3: For all rows with a variable, split/clean the variable, and designate to the appropriate columns

# Note to reviewer. I tried my best to use the apply function, but it's actually quite tricky because it involves a
# variable amount of columns with a variable amount of 'applying' based on how many splits occured per variable. 
# I couldn't figure out a way to do it- I'm sure something more efficient exists, but the below was still fast enough. 

def handle_column_split(df, og_column, og_column_prefix):
    print("Start: "+str(time.time()))
    vallist = []   # Create list to house all possible values
    
    # Step 1
    for index, row in df.iterrows():
        searchval = str(df[og_column].loc[index]) #loop through every row
        if searchval != 'nan':  # if not nan
            templist = [x.strip() for x in searchval.split(',')] # split & clean all values
            for item in templist:  # for each value not already in the master vallist
                if item not in vallist: # check
                    vallist.append(item) # then add
    # Step 2
    for i in vallist:
        df[og_column_prefix+i] = 0   # instatiate columns as int columns

    
    # Step 3
    for index, row in df.iterrows():
        searchval = str(df[og_column].loc[index]) #loop through every row
        if searchval != 'nan':  # if not nan
            templist = [x.strip() for x in searchval.split(',')]
            for item in templist:
                df[og_column_prefix+item].loc[index] = 1      #encode columns appropriately if a match

    print("End: "+str(time.time()))
    return df 

In [11]:
# Perform for all three columns:

df = handle_column_split(df,'Academy Awards','aa_')
df = handle_column_split(df,'Golden Globes','gg_')
df = handle_column_split(df,'Categories','genre_')

Start: 1526412235.3425846
End: 1526412236.594656
Start: 1526412236.596656
End: 1526412237.7697234
Start: 1526412237.7707233
End: 1526412242.3029826


In [12]:
df

Title Rating  \
0            assassination of jesse james, the      r   
1                                 dragonslayer     nr   
2                            met opera: otello     nr   
3                               finding normal     nr   
4                                        siren    NaN   
5     tyler perry's i can do bad all by myself   pg13   
6                               golden kingdom     nr   
7                                born in china      g   
8         elton john: the million dollar piano     nr   
9                                    divergent   pg13   
10                  twilight tuesdays: eclipse   pg13   
11                              father figures      r   
12                   swinging with the finkels      r   
13                      cokeville miracle, the   pg13   
14                           ava's possessions      r   
15                                        fuel     nr   
16                                reach for me     nr   
17                              lifeguard, the      r   
18                                   smothered     nr   
19                                   grey lady      r   
20                          lion of judah, the     pg   
21                                  detachment     nr   
22                        midsummer in newtown     nr   
23                                  district 9      r   
24                            cowboys & aliens   pg13   
25                               in a world...      r   
26                          as it is in heaven     nr   
27                            city of dead men     nr   
28                                 a-team, the   pg13   
29                                     armored   pg13   
30                     kurt cobain about a son     nr   
31      boys: the sherman brothers' story, the     pg   
32                           toys in the attic     pg   
33                                  vault, the     nr   
34         xaviera hollander, the happy hooker     nr   
35                          trade of innocents   pg13   
36                             time being, the     nr   
37                                     escapes     nr   
38                         welcome to lazytown      g   
39                         man from u.n.c.l.e.   pg13   
40                                willow creek    NaN   
41      electric boogaloo: the wild, untold...      r   
42                      heavy metal in baghdad     nr   
43                  john carpenter's halloween     nr   
44                                love me true      r   
45                            don't worry baby     nr   
46                                   ned rifle     nr   
47                                speed-dating      r   
48             after dark films' horrorfest iv      r   
49               ghastly love of johnny x, the     nr   
50                      forbidden kingdom, the   pg13   
51                            red machine, the    NaN   
52                           devil inside, the      r   
53                               life partners      r   
54                girl in the photographs, the      r   
55                                 snowpiercer      r   
56                            dog problem, the      r   
57                          behind the burly q     nr   
58                      providence effect, the     pg   
59      grateful dead movie (40th anniversary)   pg13   
60                            innocence (2014)   pg13   
61                                 to be heard     nr   
62          ufc 143 live in 3d: condit vs diaz     nr   
63                                endless love   pg13   
64             chris brown: welcome to my life      r   
65                      kickboxer: retaliation      r   
66               neshoba: the price of freedom     nr   
67                                      retake     nr   
68                    kirk cameron's revive us     nr   
69                                rock of ages   pg

In [13]:
# Review test case, all new values

df.iloc[182]

Title                                                                           whiplash
Rating                                                                                 r
Academy Awards                         best film editing, best sound mixing, best sup...
Actors                                 j.k. simmons, melissa benoist, miles teller, p...
Categories                                                                         drama
Detailed_Release                                                              10/10/2014
Directors                                                                damien chazelle
Dist                                                                                 spc
Distributor Long Name                                             sony pictures classics
Year(DVD/Video Release Date)                                                        2015
Golden Globes                                                      best supporting actor
Language             

In [14]:
# The remaining columns are text. Some columns that have multiple comma separated values, such as 'producers' or 'actors'.
df = df.fillna('')

In [15]:
# Review info() again
# Notice Totals columns are objects

df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7907 entries, 0 to 7906
Data columns (total 82 columns):
Title                                  7907 non-null object
Rating                                 7907 non-null object
Academy Awards                         7907 non-null object
Actors                                 7907 non-null object
Categories                             7907 non-null object
Detailed_Release                       7907 non-null object
Directors                              7907 non-null object
Dist                                   7907 non-null object
Distributor Long Name                  7907 non-null object
Year(DVD/Video Release Date)           7907 non-null object
Golden Globes                          7907 non-null object
Language                               7907 non-null object
Producers                              7907 non-null object
Production Companies                   7907 non-null object
Quarter(Release Date)                  7907 non-null 

In [16]:
# Appears that our 'Total' columns with numbers are not dtype int, but should be. Still 'object'
# Change them via pd.to_numeric after replacing errant commas 

# List of columns 
int_cols =["Total Cume", "Total DVD/Video Release Window", "Total Locs At Opening", "Total Locs At Widest Release", "Total Opening 7 Day Gross", "Total Opening Wknd Avg","Total Opening Day Gross","Total Opening Wknd Gross","Total Opening Wknd Locs","Total Run Time"]

# Try / except method used explicitly for jupyter notebook weirdness
for i in int_cols:
    try:
        x = pd.Series(df[i]).str.replace(",","")
        df[i] = pd.to_numeric(x)
    except:
        pass

In [17]:
#Backup sanity code for above 

#x = pd.Series(df['Total Opening Day Gross']).str.replace(",","")
#x = x.replace(",","")
#df['Total Opening Day Gross'] = pd.to_numeric(x)



In [18]:
# Now we see the Totals as integers
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7907 entries, 0 to 7906
Data columns (total 82 columns):
Title                                  7907 non-null object
Rating                                 7907 non-null object
Academy Awards                         7907 non-null object
Actors                                 7907 non-null object
Categories                             7907 non-null object
Detailed_Release                       7907 non-null object
Directors                              7907 non-null object
Dist                                   7907 non-null object
Distributor Long Name                  7907 non-null object
Year(DVD/Video Release Date)           7907 non-null object
Golden Globes                          7907 non-null object
Language                               7907 non-null object
Producers                              7907 non-null object
Production Companies                   7907 non-null object
Quarter(Release Date)                  7907 non-null 

In [19]:
# Rating is a valuable metric - needs to be dummified

df['Rating'].value_counts()

nr      3493
r       2057
pg13    1321
pg       596
         297
g        139
nc17       4
Name: Rating, dtype: int64

In [20]:
# Get dummies from ratings

x = pd.get_dummies(df['Rating'], prefix = "rating")
x = x.drop('rating_', axis = 1) # drop blanks as a col
df = df.join(x)
x

rating_g  rating_nc17  rating_nr  rating_pg  rating_pg13  rating_r
0            0            0          0          0            0         1
1            0            0          1          0            0         0
2            0            0          1          0            0         0
3            0            0          1          0            0         0
4            0            0          0          0            0         0
5            0            0          0          0            1         0
6            0            0          1          0            0         0
7            1            0          0          0            0         0
8            0            0          1          0            0         0
9            0            0          0          0            1         0
10           0            0          0          0            1         0
11           0            0          0          0            0         1
12           0            0          0          0            0         1
13           0            0          0          0            1         0
14           0            0          0          0            0         1
15           0            0          1          0            0         0
16           0            0          1          0            0         0
17           0            0          0          0            0         1
18           0            0          1          0            0         0
19           0            0          0          0            0         1
20           0            0          0          1            0         0
21           0            0          1          0            0         0
22           0            0          1          0            0         0
23           0            0          0          0            0         1
24           0            0          0          0            1         0
25           0            0          0          0            0         1
26           0            0          1          0            0         0
27           0            0          1          0            0         0
28           0            0          0          0            1         0
29           0            0          0          0            1         0
30           0            0          1          0            0         0
31           0            0          0          1            0         0
32           0            0          0          1            0         0
33           0            0          1          0            0         0
34           0            0          1          0            0         0
35           0            0          0          0            1         0
36           0            0          1          0            0         0
37           0            0          1          0            0         0
38           1            0          0          0            0         0
39           0            0          0          0            1         0
40           0            0          0          0            0         0
41           0            0          0          0            0         1
42           0            0          1          0            0         0
43           0            0          1          0            0         0
44           0            0          0          0            0         1
45           0            0          1          0            0         0
46           0            0          1          0            0         0
47           0            0          0          0            0         1
48           0            0          0          0            0         1
49           0            0          1          0            0         0
50           0            0          0          0            1         0
51           0            0          0          0            0         0
52           0            0          0          0            0         1
53           0            0          0          0            0  

In [21]:
# Get dummies from distributor 

x = pd.get_dummies(df['Dist'], prefix = "dist")
df = df.join(x)
x

dist_11arts  dist_5&2  dist_7arts  dist_7flr  dist_a23  dist_a24  \
0               0         0           0          0         0         0   
1               0         0           0          0         0         0   
2               0         0           0          0         0         0   
3               0         0           0          0         0         0   
4               0         0           0          0         0         0   
5               0         0           0          0         0         0   
6               0         0           0          0         0         0   
7               0         0           0          0         0         0   
8               0         0           0          0         0         0   
9               0         0           0          0         0         0   
10              0         0           0          0         0         0   
11              0         0           0          0         0         0   
12              0         0           0          0         0         0   
13              0         0           0          0         0         0   
14              0         0           0          0         0         0   
15              0         0           0          0         0         0   
16              0         0           0          0         0         0   
17              0         0           0          0         0         0   
18              0         0           0          0         0         0   
19              0         0           0          0         0         0   
20              0         0           0          0         0         0   
21              0         0           0          0         0         0   
22              0         0           0          0         0         0   
23              0         0           0          0         0         0   
24              0         0           0          0         0         0   
25              0         0           0          0         0         0   
26              0         0           0          0         0         0   
27              0         0           0          0         0         0   
28              0         0           0          0         0         0   
29              0         0           0          0         0         0   
30              0         0           0          0         0         0   
31              0         0           0          0         0         0   
32              0         0           0          0         0         0   
33              0         0           0          0         0         0   
34              0         0           0          0         0         0   
35              0         0           0          0         0         0   
36              0         0           0          0         0         0   
37              0         0           0          0         0         0   
38              0         0           0          0         0         0   
39              0         0           0          0         0         0   
40              0         0           0          0         0         0   
41              0         0           0          0         0         0   
42              0         0           0          0         0         0   
43              0         0           0          0         0         0   
44              0         0           0          0         0         0   
45              0         0           0          0         0         0   
46              0         0           0          0         0         0   
47              0         0           0          0         0         0   
48              0         0           0          0         0         0   
49              0         0           0          0         0         0   
50              0         0           0          0         0         0   
51              0         0           0          0         0         0   
52              0         0           0          0         0         0   
53        

In [22]:
# Finally, review data columns one last time
# Dummifying both rating and distributor causes a TON of features. Distributor may be dropped later, but it is still interesting.

print( df.columns.tolist() )


['Title', 'Rating', 'Academy Awards', 'Actors', 'Categories', 'Detailed_Release', 'Directors', 'Dist', 'Distributor Long Name', 'Year(DVD/Video Release Date)', 'Golden Globes', 'Language', 'Producers', 'Production Companies', 'Quarter(Release Date)', 'Sound Formats', 'Visual Formats', 'Writers', 'Total Cume', 'Total DVD/Video Release Window', 'Total Locs At Opening', 'Total Locs At Widest Release', 'Total Opening 7 Day Gross', 'Total Opening Day Gross', 'Total Opening Wknd Avg', 'Total Opening Wknd Gross', 'Total Opening Wknd Locs', 'Total Run Time', 'aa_best actress', 'aa_best art direction', 'aa_best cinematography', 'aa_best director', 'aa_best score', 'aa_best song', 'aa_best film editing', 'aa_best sound mixing', 'aa_best supporting actor', 'aa_best costume design', 'aa_best makeup', 'aa_best sound editing', 'aa_best documentary', 'aa_best adapted screenplay', 'aa_best picture', 'aa_best actor', 'aa_best supporting actress', 'aa_best animated feature film', 'aa_best original scree

In [23]:
# Release date needs to be sanitized:

df['Detailed_Release']

0              9/21/2007
1              11/4/2011
2       10/27/2012 (sat)
3              7/27/2007
4              12/2/2016
5              9/11/2009
6              6/17/2016
7              4/21/2017
8       03/18/2014 (tue)
9              3/21/2014
10      11/15/2011 (tue)
11            12/22/2017
12             8/26/2011
13              6/5/2015
14      03/03/2016 (thu)
15            11/14/2008
16            12/18/2009
17             8/30/2013
18              4/8/2016
19             4/28/2017
20              6/3/2011
21             3/16/2012
22             1/27/2017
23             8/14/2009
24             7/29/2011
25              8/9/2013
26             7/11/2014
27            12/16/2016
28             6/11/2010
29             12/4/2009
30      10/03/2007 (wed)
31             5/22/2009
32              9/7/2012
33              9/1/2017
34             1/29/2010
35             10/5/2012
36             7/26/2013
37      07/26/2017 (wed)
38      11/03/2012 (sat)
39             8/14/2015


In [24]:
# Develop regex pattern to find these cases below:

y = "10/27/2012 (sat)"
pattern = r"(?P<one>\d\d/\d\d/\d\d\d\d)+(\s\(\w\w\w\))+"

re.match(pattern, y)

<_sre.SRE_Match object; span=(0, 16), match='10/27/2012 (sat)'>

In [25]:
x = df['Detailed_Release']
repl = lambda m: m.group('one')

x = x.str.replace(pattern, repl)
x

0        9/21/2007
1        11/4/2011
2       10/27/2012
3        7/27/2007
4        12/2/2016
5        9/11/2009
6        6/17/2016
7        4/21/2017
8       03/18/2014
9        3/21/2014
10      11/15/2011
11      12/22/2017
12       8/26/2011
13        6/5/2015
14      03/03/2016
15      11/14/2008
16      12/18/2009
17       8/30/2013
18        4/8/2016
19       4/28/2017
20        6/3/2011
21       3/16/2012
22       1/27/2017
23       8/14/2009
24       7/29/2011
25        8/9/2013
26       7/11/2014
27      12/16/2016
28       6/11/2010
29       12/4/2009
30      10/03/2007
31       5/22/2009
32        9/7/2012
33        9/1/2017
34       1/29/2010
35       10/5/2012
36       7/26/2013
37      07/26/2017
38      11/03/2012
39       8/14/2015
40        6/6/2014
41      09/17/2015
42       5/23/2008
43      10/29/2015
44       8/12/2016
45       7/22/2016
46      04/01/2015
47        6/4/2010
48       1/29/2010
49      10/26/2012
50       4/18/2008
51       10/1/2010
52        1/

In [26]:
# drop 'unset' to nulls
x = x.str.replace('unset', '')
x

0        9/21/2007
1        11/4/2011
2       10/27/2012
3        7/27/2007
4        12/2/2016
5        9/11/2009
6        6/17/2016
7        4/21/2017
8       03/18/2014
9        3/21/2014
10      11/15/2011
11      12/22/2017
12       8/26/2011
13        6/5/2015
14      03/03/2016
15      11/14/2008
16      12/18/2009
17       8/30/2013
18        4/8/2016
19       4/28/2017
20        6/3/2011
21       3/16/2012
22       1/27/2017
23       8/14/2009
24       7/29/2011
25        8/9/2013
26       7/11/2014
27      12/16/2016
28       6/11/2010
29       12/4/2009
30      10/03/2007
31       5/22/2009
32        9/7/2012
33        9/1/2017
34       1/29/2010
35       10/5/2012
36       7/26/2013
37      07/26/2017
38      11/03/2012
39       8/14/2015
40        6/6/2014
41      09/17/2015
42       5/23/2008
43      10/29/2015
44       8/12/2016
45       7/22/2016
46      04/01/2015
47        6/4/2010
48       1/29/2010
49      10/26/2012
50       4/18/2008
51       10/1/2010
52        1/

In [27]:
# Finally, convert to date time, allowing nulls to be NaT, and add back to dataframe
x = pd.to_datetime(x, errors='coerce')
df['Detailed_Release'] = x

In [ ]:
# Save a version to work with for the future. Checkpoint to avoid processing above code over and over. 
# df.to_csv('data/filmgrosses_clean_1.csv', index=False)

## Web scraping via metacritic

Refer to webscraper iPython notebook "pm_webscraper_v2" in this repo. The goal is to bring in metacritic data to use as a primary feature for the model. A webscraper was built to attempt to retrieve as many metacritic scores for as many films as possible. 

In [ ]:
#Load checkpoint
df= pd.read_csv('data/filmgrosses_clean_1.csv')

In [29]:
df_metacritic = pd.read_csv('data/metacritic_scores.csv')

### Cleaning titles

In the filmgrosses data, the titles need to be cleaned to not have ", the" at the end, or end in dates "(2007)"

In [30]:
# There are 11k metacritic films, which go back to ~1960s/70s in film, but 8k in the filmgrosses from 2007. Naturally,
#    some titles in the filmgrosses won't have matches. 

titles = df_metacritic['title']

In [31]:
# Need to clean titles from filmgrosses that end with ', the' and "(2007)" using regex. Will help fuzzy matcher tremendously

def clean_title_endings(x):
    if ', the' in x:
        x = x.strip()
        match_pattern = r"(.*)(the)$"
        replace_pattern = '\g<2> \g<1>'
        compiler = re.compile(match_pattern)
        return compiler.sub(replace_pattern, x).strip()[:-1]
    elif ', a' in x:
        x = x.strip()
        match_pattern = r"(.*)(a)$"
        replace_pattern = '\g<2> \g<1>'
        compiler = re.compile(match_pattern)
        return compiler.sub(replace_pattern, x).strip()[:-1]
    else:
        return x

def clean_title_year(x):
    x = x.strip()
    match_pattern = r"(.*)(\(\d\d\d\d\)$)"
    replace_pattern = '\g<1>'
    compiler = re.compile(match_pattern)
    return compiler.sub(replace_pattern, x).strip()

In [32]:
# Test on 10 rows quickly:

df_x = df[['Title']][200:210]
df_x['Title_clean'] = df_x['Title'].apply(clean_title_year)
df_x['Title_clean_2'] = df_x['Title_clean'].apply(clean_title_endings)
df_x

Title  \
200                      x games 3d the movie   
201                            overnight, the   
202  fathom premieres: 6 below: miracle on th   
203                                    revolt   
204                          bless me, ultima   
205                                 reason, a   
206                                 highwater   
207                     chameleon, the (2010)   
208          midnight man, the (dir. zariwny)   
209                         letters to juliet   

                                  Title_clean  \
200                      x games 3d the movie   
201                            overnight, the   
202  fathom premieres: 6 below: miracle on th   
203                                    revolt   
204                          bless me, ultima   
205                                 reason, a   
206                                 highwater   
207                            chameleon, the   
208          midnight man, the (dir. zariwny)   
209                         letters to juliet   

                                Title_clean_2  
200                      x games 3d the movie  
201                             the overnight  
202  fathom premieres: 6 below: miracle on th  
203                                    revolt  
204                          bless me, ultima  
205                                  a reason  
206                                 highwater  
207                             the chameleon  
208           midnight man, the (dir. zariwny  
209                         letters to juliet

In [33]:
df['clean_Title'] = df['Title'].apply(clean_title_year)
df['clean_Title'] = df['clean_Title'].apply(clean_title_endings)
df

Title Rating  \
0            assassination of jesse james, the      r   
1                                 dragonslayer     nr   
2                            met opera: otello     nr   
3                               finding normal     nr   
4                                        siren          
5     tyler perry's i can do bad all by myself   pg13   
6                               golden kingdom     nr   
7                                born in china      g   
8         elton john: the million dollar piano     nr   
9                                    divergent   pg13   
10                  twilight tuesdays: eclipse   pg13   
11                              father figures      r   
12                   swinging with the finkels      r   
13                      cokeville miracle, the   pg13   
14                           ava's possessions      r   
15                                        fuel     nr   
16                                reach for me     nr   
17                              lifeguard, the      r   
18                                   smothered     nr   
19                                   grey lady      r   
20                          lion of judah, the     pg   
21                                  detachment     nr   
22                        midsummer in newtown     nr   
23                                  district 9      r   
24                            cowboys & aliens   pg13   
25                               in a world...      r   
26                          as it is in heaven     nr   
27                            city of dead men     nr   
28                                 a-team, the   pg13   
29                                     armored   pg13   
30                     kurt cobain about a son     nr   
31      boys: the sherman brothers' story, the     pg   
32                           toys in the attic     pg   
33                                  vault, the     nr   
34         xaviera hollander, the happy hooker     nr   
35                          trade of innocents   pg13   
36                             time being, the     nr   
37                                     escapes     nr   
38                         welcome to lazytown      g   
39                         man from u.n.c.l.e.   pg13   
40                                willow creek          
41      electric boogaloo: the wild, untold...      r   
42                      heavy metal in baghdad     nr   
43                  john carpenter's halloween     nr   
44                                love me true      r   
45                            don't worry baby     nr   
46                                   ned rifle     nr   
47                                speed-dating      r   
48             after dark films' horrorfest iv      r   
49               ghastly love of johnny x, the     nr   
50                      forbidden kingdom, the   pg13   
51                            red machine, the          
52                           devil inside, the      r   
53                               life partners      r   
54                girl in the photographs, the      r   
55                                 snowpiercer      r   
56                            dog problem, the      r   
57                          behind the burly q     nr   
58                      providence effect, the     pg   
59      grateful dead movie (40th anniversary)   pg13   
60                            innocence (2014)   pg13   
61                                 to be heard     nr   
62          ufc 143 live in 3d: condit vs diaz     nr   
63                                endless love   pg13   
64             chris brown: welcome to my life      r   
65                      kickboxer: retaliation      r   
66               neshoba: the price of freedom     nr   
67                                      retake     nr   
68                    kirk cameron's revive us     nr   
69                                rock of ages   pg

### Fuzzy matching

These titles will need to be matched to the filmgrosses data set.   
A fuzzy search will best accomplish. Aftewards, we'll have to drop the non-matches.  
Unfortunately, the risk of duplication of titles (different films w/ the exact same title per metacritic) exists

A fuzz.ratio score of 90 was decided by doing some checks back and forth against both data sets. This seems to be the best balance of both scorer (there are multiple 'scorers' for fuzzy selection, the default being most applicable), and to be reasonably accurate with 90.

In [34]:
def check_ratio(x):
    y = process.extract(x, titles, scorer=fuzz.ratio)[0]
    if y[1]>90:
        return y[0]
    else:
        return ''

In [35]:
# Test on 10 titles. 
df_test = df[200:210].copy()
df_test['match_title'] = df_test['clean_Title'].apply(check_ratio)

In [37]:
df_test[['clean_Title','match_title']]

clean_Title            match_title
200                      x games 3d the movie  X Games 3D: The Movie
201                             the overnight          The Overnight
202  fathom premieres: 6 below: miracle on th                       
203                                    revolt                       
204                          bless me, ultima       Bless Me, Ultima
205                                  a reason                       
206                                 highwater                       
207                             the chameleon                       
208           midnight man, the (dir. zariwny                       
209                         letters to juliet      Letters to Juliet

In [ ]:
# Perform for whole dataframe:
df['match_title'] = df['clean_Title'].apply(check_ratio)

In [ ]:
# Another checkpoint (the above matching took a while)
# df.to_csv('data/filmgrosses_clean_2.csv', index=False)

### Merge data sets
Now it's time to take matched titles and return the metacritic scores. This will reduce the # of titles significantly.

In [38]:
# Load for checkpoint
df = pd.read_csv('data/filmgrosses_clean_2.csv')
df_metacritic = pd.read_csv('data/metacritic_scores.csv')

In [39]:
# Select only matched titles, and those with more than 0 cume
df_mod = df.loc[df['match_title'].isnull() == False]
df_mod = df_mod.loc[df['Total Cume'] >= 0]

In [40]:
df_mod.shape

(4154, 477)

In [41]:
df_join = df_mod.merge(df_metacritic, left_on = 'match_title', right_on = 'title')

In [42]:
df = df_join.drop(['title'], axis = 1)

# Modeling
After ALL the cleaning, finally time to take a look at some different modeling potential.

In [43]:
# Now, let's experiment with metrics
# Preliminarily use 'total cume' as y variable
corr_map = df.corr()

In [44]:
# To clarify, Total Cume is the target variable. The other grosses and opening location 
# numbers are so obviously correlated, that they aren't considered in the model. They could be their own
# target variables for the analysis. 

corr_map['Total Cume'].sort_values(ascending = False)

Total Cume                             1.000000
Total Opening 7 Day Gross              0.945637
Total Opening Wknd Gross               0.928430
Total Opening Day Gross                0.894761
Total Locs At Widest Release           0.697665
Total Opening Wknd Locs                0.663998
Total Locs At Opening                  0.662945
genre_adventure                        0.450099
dist_dis                               0.343908
Total Opening Wknd Avg                 0.338051
genre_action                           0.325096
genre_fantasy                          0.317618
genre_family                           0.290852
Total Run Time                         0.278334
genre_animation                        0.275069
genre_science fiction                  0.263120
rating_pg13                            0.254576
aa_best animated feature film          0.234731
dist_wb                                0.222726
rating_pg                              0.204814
dist_fox                               0

In [46]:
df_model = df_join.select_dtypes(include='int64') # Choose only int dtypes 
df_model = df_model.drop(['Total Opening 7 Day Gross', 'Total Opening Day Gross', 'Total Opening Wknd Gross', 'Total Opening Wknd Locs','Total Locs At Opening','Total Locs At Widest Release','Total Opening Wknd Avg','Total DVD/Video Release Window'], axis = 1)

In [47]:
df_model.columns.tolist()

['Total Cume',
 'Total Run Time',
 'aa_best actress',
 'aa_best art direction',
 'aa_best cinematography',
 'aa_best director',
 'aa_best score',
 'aa_best song',
 'aa_best film editing',
 'aa_best sound mixing',
 'aa_best supporting actor',
 'aa_best costume design',
 'aa_best makeup',
 'aa_best sound editing',
 'aa_best documentary',
 'aa_best adapted screenplay',
 'aa_best picture',
 'aa_best actor',
 'aa_best supporting actress',
 'aa_best animated feature film',
 'aa_best original screenplay',
 'aa_best visual effects',
 'aa_best foreign language film',
 'gg_best actor - musical or comedy',
 'gg_best actress - musical or comedy',
 'gg_best director',
 'gg_best picture - musical or comedy',
 'gg_best screenplay',
 'gg_best supporting actor',
 'gg_best picture - drama',
 'gg_best actor - drama',
 'gg_best supporting actress',
 'gg_best actress - drama',
 'genre_drama',
 'genre_action',
 'genre_western',
 'genre_documentary',
 'genre_special events',
 'genre_horror',
 'genre_comedy',

## Model selection:

Primary choice for model based on dataset will be a logistic regression. Not only are we attempting to create a predictive model, this dataset now has many features, and is relatively straightforward in it's design. I believe a logistic regression to be the smartest approach to the idea of estimating box office grosses based on metacritic scores, genres, ratings and distributors.

In [48]:
# First pass - try a model simply with metacritic score & Total Cume
X = df_model['metacritic_score'].reshape(-1,1)
y = df_model['Total Cume']  # Total Cume

In [49]:
# Clearly, not a strong model as a baseline. This score is quite low - perhaps there is not much predictive power
# in metacritic scores.
X_train, X_test, y_train, y_test = train_test_split(X, y) 

lgr = LogisticRegression()
lgr.fit(X_train,y_train)
lgr.score(X_train,y_train)

0.18089053803339517

In [50]:
# However, let's scale the data appropriately and try some other techniques. 
# df_model2 drops 'Total Cume'

df_model2 = df_model[['metacritic_score']]
cols = df_model2.columns

std_scaled = StandardScaler()
minmax_scaled = MinMaxScaler()

std_df = std_scaled.fit_transform(df_model2[[name for name in cols]])
minmax_df = minmax_scaled.fit_transform(df_model2[[name for name in cols]])

In [17]:
# Try again. 

X = std_df
y = df_model['Total Cume']  # Total Cume

X_train, X_test, y_train, y_test = train_test_split(X, y) 

lgr = LogisticRegression()
lgr.fit(X_train,y_train)
print("Standard scaler: "+str(lgr.score(X_train,y_train)))

X = minmax_df

X_train, X_test, y_train, y_test = train_test_split(X, y)

lgr = LogisticRegression()
lgr.fit(X_train,y_train)
print("Minmax scaler: "+str(lgr.score(X_train,y_train)))

Standard scaler: 0.17934446505875076
Minmax scaler: 0.17841682127396413


In [51]:
# These did not help specifically with metacritic scores, but perhaps will help greatly with other features.
# Let's proceed with using the standard scaler for the whole dataset. 

std_scaled = StandardScaler()
df_model2 = df_model.drop(['Total Cume'], axis = 1)
cols = df_model2.columns
std_df = std_scaled.fit_transform(df_model2[[name for name in cols]])

In [52]:
# Let's reduce the features to a reasonable level (rather than 450+ features), using scaled data.

feature_pct = range(10,110) 

X = std_df
y = df_model['Total Cume']  # Total Cume
X_train, X_test, y_train, y_test = train_test_split(X, y) 

In [30]:
for i in feature_pct[0::10]:
    select = SelectPercentile(percentile=i)
    select.fit(X_train, y_train)
    X_train_selected = select.transform(X_train)
    lgr = LogisticRegression()
    lgr.fit(X_train_selected, y_train)
    print("Score at "+str(i)+"% feature percentage: "+str(lgr.score(X_train_selected,y_train)))

Score at 10% feature percentage: 0.21119356833642547
Score at 20% feature percentage: 0.23067408781694496
Score at 30% feature percentage: 0.24675324675324675
Score at 40% feature percentage: 0.37755102040816324
Score at 50% feature percentage: 0.6533704390847248
Score at 60% feature percentage: 0.678726035868893
Score at 70% feature percentage: 0.7158317872603587
Score at 80% feature percentage: 0.7204700061842919
Score at 90% feature percentage: 0.7204700061842919
Score at 100% feature percentage: 0.7204700061842919


In [54]:
# So, 80% features it is. 

select = SelectPercentile(percentile=80)
select.fit(X_train, y_train)
X_train_selected = select.transform(X_train)

In [27]:
# Let's entertain the idea of using a regularized method
for alpha in [.25,.5,.75,1,1.25,1.5,1.75,2,2.25,2.5,2.75,3]:
    ridge_reg = Ridge(alpha = alpha, solver = "cholesky")
    lasso_reg = Lasso(alpha = alpha)
    elastic_reg = ElasticNet(alpha = alpha)
    regs = {'Ridge':ridge_reg,"Lasso":lasso_reg, "Elast":elastic_reg}
    for i in regs:
        regs[i].fit(X_train_selected, y_train)
        print("Regression "+str(i)+" | alpha "+str(alpha)+" "+str(regs[i].score(X_train_selected, y_train)))



Regression Ridge | alpha 0.25 0.5931494339280925
Regression Lasso | alpha 0.25 0.5931494627033479
Regression Elast | alpha 0.25 0.5872877846416342
Regression Ridge | alpha 0.5 0.5931493488672088
Regression Lasso | alpha 0.5 0.593149462703314
Regression Elast | alpha 0.5 0.578939525704363
Regression Ridge | alpha 0.75 0.5931492093628059
Regression Lasso | alpha 0.75 0.5931494627032576
Regression Elast | alpha 0.75 0.5700300621457288
Regression Ridge | alpha 1 0.59314901718584
Regression Lasso | alpha 1 0.5931494627031788
Regression Elast | alpha 1 0.5609899599167931
Regression Ridge | alpha 1.25 0.5931487740391996
Regression Lasso | alpha 1.25 0.5931494627030773
Regression Elast | alpha 1.25 0.5519825492354522
Regression Ridge | alpha 1.5 0.5931484815606319
Regression Lasso | alpha 1.5 0.5931494627029535
Regression Elast | alpha 1.5 0.5430841581011077
Regression Ridge | alpha 1.75 0.5931481413255253
Regression Lasso | alpha 1.75 0.5931494627028071
Regression Elast | alpha 1.75 0.5343345

In [ ]:
# Ridge and Lasso clearly better than Elastic, but all worse than logistic regression. 

In [56]:
# Let's cross validate 80% features logistic regression
lgr_scores = cross_val_score(lgr, X_train_selected, y_train, scoring = "neg_mean_squared_error", cv = 5)

In [62]:
rmse_scores = np.sqrt(-lgr_scores)
rmse_scores.mean()

# Definitely room for improvement:

20603586.26987833

 This is where the notebook ends. Some work will be done to clean up for   
 the final presentation, mostly to show some final graphs and to consider  
 what a very robust model would look like (and how much effort it would take to get there). 
